In [ ]:
#!pip install selenium
#!pip install bs4
# chorme driver.exe 설치
# https://chromedriver.chromium.org/downloads

In [60]:
from selenium import webdriver
from selenium.webdriver import Chrome
from selenium.common.exceptions import WebDriverException as WDE
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
import requests
from bs4 import BeautifulSoup
import time
import pandas as pd
from selenium.common.exceptions import NoSuchElementException

In [65]:
# 페이지 안의 주소 담기
def extract_address_info(browser, df) : 
    # 가져온 HTML을 파싱하기
    soup = BeautifulSoup(browser.page_source, 'html.parser') # lxml

    # 주소 정보 리스트를 담고 있는 <ol> 태그 찾기
    address_list = soup.find('ol')

    # <li class="inner_addr"> 태그 찾기
    # address_list가 존재하면(값이 None이 아니라면), 앞 코드 실행하여 결과를 inner_addr_list에 저장
    # 그렇지 않다면 (address_list가 None이라면), inner_addr_list에 빈 리스트 []를 저장
    inner_addr_list = address_list.find_all('li', class_='inner_addr') if address_list else []

    # 각 <li> 태그 안의 <div class="subject_1">의 도로명 주소와
    # <div class="subject_2">의 지번 주소를 찾아 출력
    for inner_addr in inner_addr_list :
        subejct_1_div = inner_addr.find('div', class_='subejct_1')
        subeject_2_div = inner_addr.find('div', class_='subejct_2')
        
        # subject_1_div가 존재하면
        if subejct_1_div: 
            # <span class="roadNameText"> 찾아서 road_name_text_1 변수에 할당
            road_name_text_1 = subejct_1_div.find('span', class_='roadNameText')
            # 공백제거 & &nbsp; 문자(띄어쓰기를 나타내는 HTML 엔티티)를 일반 공백 문자로 대체
            text_1 = ' '.join(road_name_text_1.stripped_strings).replace(u'/xa0', u' ')
            # print(f"도로명주소: {text_1}")
        else:
            text_1 = None
        
        if subeject_2_div:
            road_name_text_2 = subeject_2_div.find('span', class_='roadNameText')
            text_2 = ' '.join(road_name_text_2.stripped_strings)
        else:
            text_2 = None

        # 해당 행을 데이터프레임에 추가
        df = df.append({'도로명주소': text_1, '지번주소': text_2}, ignore_index=True)
    
    return df
    

In [69]:
def click_page_number(browser, page_number):
    try:
        page_button = browser.find_element(By.CSS_SELECTOR, f'a[title="{page_number}페이지"]')
        page_button.click()
        time.sleep(1)
        return True
    except NoSuchElementException:
        return False

def click_next_page_set(browser):
    try:
        next_page_set_button = browser.find_element(By.CSS_SELECTOR, 'a.skip_txt.next')
        next_page_set_button.click()
        time.sleep(1)
        return True
    except NoSuchElementException:
        return False

In [70]:
## 준비 설정
# 접속 url
url = "https://www.juso.go.kr/support/AddressMainSearch.do?firstSort=none&ablYn=N&aotYn=N&fillterHiddenValue=&searchKeyword=%EC%84%9C%EC%9A%B8%ED%8A%B9%EB%B3%84%EC%8B%9C+%EA%B4%91%EC%A7%84%EA%B5%AC&dsgubuntext=&dscity1text=&dscounty1text=&dsemd1text=&dsri1text=&dssan1text=&dsrd_nm1text=&searchType=HSTRY&dssearchType1=road&dscity1=&dscounty1=&dsrd_nm_idx1=%EA%B0%80_%EB%82%98&dsrd_nm1=&dsma=&dssb=&dstown1=&dsri1=&dsbun1=&dsbun2=&dstown2=&dsbuilding1="

# 주소명 검색 홈페이지 접속
path = 'C:/Python_practice/DL_project/music_resting_place_ver_dh/0. dataset/chromedriver_win32/chromedriver.exe'
browser = Chrome(executable_path=path) # 개인에게 맞는 경로 수정 필요
browser.get(url)

# 데이터 프레임 형성
df = pd.DataFrame(columns = ['도로명주소', '지번주소'])

current_page = 1
last_page = 2344
while current_page <= last_page:
    df = extract_address_info(browser, df)
    current_page += 1

    if not click_page_number(browser, current_page):
        if not click_next_page_set(browser):
            break

# 마지막 페이지 2344에서 종료가 안되고 계속 반복 크롤링하여 강제 종료함 (이 부분은 별도 코드 수정 필요)
# 브라우저 종료
browser.quit()

C:\Users\dohee\AppData\Local\Temp\ipykernel_5408\1727922648.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  browser = Chrome(executable_path=path) # 개인에게 맞는 경로 수정 필요
C:\Users\dohee\AppData\Local\Temp\ipykernel_5408\2776431490.py:37: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'도로명주소': text_1, '지번주소': text_2}, ignore_index=True)
C:\Users\dohee\AppData\Local\Temp\ipykernel_5408\2776431490.py:37: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'도로명주소': text_1, '지번주소': text_2}, ignore_index=True)
C:\Users\dohee\AppData\Local\Temp\ipykernel_5408\2776431490.py:37: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'도로명주소': text_1, '지번주소': 

NoSuchWindowException: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=111.0.5563.148)
Stacktrace:
Backtrace:
	(No symbol) [0x006137D3]
	(No symbol) [0x005A8B81]
	(No symbol) [0x004AB36D]
	(No symbol) [0x0048E5DA]
	(No symbol) [0x004FF0CB]
	(No symbol) [0x00510A56]
	(No symbol) [0x004FB216]
	(No symbol) [0x004D0D97]
	(No symbol) [0x004D253D]
	GetHandleVerifier [0x0088ABF2+2510930]
	GetHandleVerifier [0x008B8EC1+2700065]
	GetHandleVerifier [0x008BC86C+2714828]
	GetHandleVerifier [0x006C3480+645344]
	(No symbol) [0x005B0FD2]
	(No symbol) [0x005B6C68]
	(No symbol) [0x005B6D4B]
	(No symbol) [0x005C0D6B]
	BaseThreadInitThunk [0x75AA00F9+25]
	RtlGetAppContainerNamedObjectPath [0x76F87BBE+286]
	RtlGetAppContainerNamedObjectPath [0x76F87B8E+238]


In [71]:
df


도로명주소  \
0         서울특별시 광진구 강변북로 2140 (자양동)   
1         서울특별시 광진구 강변북로 2160 (자양동)   
2         서울특별시 광진구 강변북로 2184 (자양동)   
3         서울특별시 광진구 강변북로 2198 (자양동)   
4         서울특별시 광진구 강변북로 2202 (자양동)   
...                             ...   
23467   서울특별시 광진구 천호대로143길 29 (광장동)   
23468   서울특별시 광진구 천호대로143길 30 (광장동)   
23469   서울특별시 광진구 천호대로143길 33 (광장동)   
23470   서울특별시 광진구 천호대로143길 34 (광장동)   
23471  서울특별시 광진구 천호대로145길 8-7 (광장동)   

                                                    지번주소  
0                                  서울특별시 광진구 자양동  158-17  
1      서울특별시 광진구 자양동  131\n\t\t\t\t\t\t\t\t\t\t\t\t\t...  
2                                     서울특별시 광진구 자양동  131  
3                                   서울특별시 광진구 자양동  133-2  
4      서울특별시 광진구 자양동  97-5\n\t\t\t\t\t\t\t\t\t\t\t\t\...  
...                                                  ...  
23467                              서울특별시 광진구 광장동  257-10  
23468                               서울특별시 광진구 광장동  256-1  
23469                               서울특별시 광진구 광장동  257-5  
23470                               서울특별시 광진구 광장동  257-4  
23471                              서울특별시 광진구 광장동  243-12  

[23472 rows x 2 columns]

In [75]:
df.to_excel('C:/Python_practice/DL_project/gwangjin_contest/광진구_지번.xlsx', index=0)

In [81]:
csv_df = pd.read_excel('C:/Python_practice/DL_project/gwangjin_contest/광진구_지번.xlsx')
csv_df.to_csv('C:/Python_practice/DL_project/gwangjin_contest/광진구_지번.csv', index=0)

In [84]:
pd.read_csv('C:/Python_practice/DL_project/gwangjin_contest/광진구_지번.csv')


도로명주소  \
0         서울특별시 광진구 강변북로 2140 (자양동)   
1         서울특별시 광진구 강변북로 2160 (자양동)   
2         서울특별시 광진구 강변북로 2184 (자양동)   
3         서울특별시 광진구 강변북로 2198 (자양동)   
4         서울특별시 광진구 강변북로 2202 (자양동)   
...                             ...   
23431   서울특별시 광진구 천호대로143길 29 (광장동)   
23432   서울특별시 광진구 천호대로143길 30 (광장동)   
23433   서울특별시 광진구 천호대로143길 33 (광장동)   
23434   서울특별시 광진구 천호대로143길 34 (광장동)   
23435  서울특별시 광진구 천호대로145길 8-7 (광장동)   

                                                    지번주소  
0                                  서울특별시 광진구 자양동  158-17  
1      서울특별시 광진구 자양동  131\n\t\t\t\t\t\t\t\t\t\t\t\t\t...  
2                                     서울특별시 광진구 자양동  131  
3                                   서울특별시 광진구 자양동  133-2  
4      서울특별시 광진구 자양동  97-5\n\t\t\t\t\t\t\t\t\t\t\t\t\...  
...                                                  ...  
23431                              서울특별시 광진구 광장동  257-10  
23432                               서울특별시 광진구 광장동  256-1  
23433                               서울특별시 광진구 광장동  257-5  
23434                               서울특별시 광진구 광장동  257-4  
23435                              서울특별시 광진구 광장동  243-12  

[23436 rows x 2 columns]